In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf
from skimage.feature import local_binary_pattern

tf.logging.set_verbosity(tf.logging.INFO)

# Our application logic will be added here

In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2 and Pooling Layer #2
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Dense Layer
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits Layer
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }

  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [3]:
def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
  # Create train_data after lbp feature extraction
  train_data_reshape = train_data.reshape(train_data.shape[0], 28, 28)
 
  train_data_reshape_lbp = []
  train_data_lbp = []
  for i in range(train_data_reshape.shape[0]):
      train_data_reshape_lbp.append(np.float32(local_binary_pattern(train_data_reshape[i], 8, 1, method='ror')))
      train_data_lbp.append(train_data_reshape_lbp[i].flatten())

  train_data_reshape_lbp = np.array(train_data_reshape_lbp)
  train_data_lbp = np.array(train_data_lbp)
  print("The train data have made LBP feature extraction")

  # Create eval_data after lbp feature extraction
  eval_data_reshape = eval_data.reshape(eval_data.shape[0], 28, 28)
 
  eval_data_reshape_lbp = []
  eval_data_lbp = []
  for i in range(eval_data_reshape.shape[0]):
      eval_data_reshape_lbp.append(np.float32(local_binary_pattern(eval_data_reshape[i], 8, 1, method='ror')))
      eval_data_lbp.append(eval_data_reshape_lbp[i].flatten())

  eval_data_reshape_lbp = np.array(eval_data_reshape_lbp)
  eval_data_lbp = np.array(eval_data_lbp)
  print("The train data have made LBP feature extraction")
  
  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="tmp/lbp_cnn_mnist_2")
  
  # Set up logging for predictions
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data_lbp},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
  mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])
    
  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data_lbp},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

In [4]:
if __name__ == "__main__":
  tf.app.run()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
The train data have made LBP feature extraction
The train data have made LBP feature extraction
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_summary_steps': 100, '_save_checkpoints_secs': 600, '_log_step_count_steps': 100, '_tf_random_seed': 1, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_save_checkpoints_steps': None, '_session_config': None, '_model_dir': 'tmp/lbp_cnn_mnist_2'}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into tmp/lbp_cnn_mnist_2/model.ckpt.
INFO:tensorflow:probabilities = [[ 0.          1.          0.          0.          0.          0.          0.
   0.          0.          0.        ]
 [ 0.          1.          0.          0.          0.          0.          0.
   0.          0. 

INFO:tensorflow:step = 1, loss = 104.386
INFO:tensorflow:probabilities = [[ 0.10913298  0.06284985  0.08792182  0.13587214  0.09008145  0.05130471
   0.13511148  0.11445867  0.09503184  0.11823508]
 [ 0.09979837  0.10051552  0.09989835  0.099857    0.10008119  0.10025612
   0.09977769  0.09978803  0.10031566  0.09971201]
 [ 0.11781262  0.04148894  0.11209291  0.13530667  0.0750855   0.02946412
   0.15041667  0.16386819  0.0510773   0.12338708]
 [ 0.10807812  0.06662981  0.1027108   0.10766351  0.10843872  0.08661866
   0.11077656  0.10255264  0.09533978  0.11119136]
 [ 0.11267885  0.06143526  0.10466076  0.11769469  0.11251967  0.05548662
   0.10879352  0.11413033  0.08572882  0.1268715 ]
 [ 0.1082065   0.06825911  0.11254249  0.11146428  0.10660455  0.05761075
   0.12382193  0.11720073  0.08323009  0.11105958]
 [ 0.09283408  0.04357996  0.13344087  0.14150876  0.11399245  0.06651717
   0.14382556  0.09270769  0.07948213  0.09211126]
 [ 0.08655483  0.0608305   0.10132227  0.11377225  0

INFO:tensorflow:global_step/sec: 5.40365
INFO:tensorflow:probabilities = [[ 0.14769362  0.03205625  0.09349455  0.12747552  0.08463971  0.04503782
   0.14499389  0.11705685  0.06043833  0.14711341]
 [ 0.10866287  0.08915403  0.09853937  0.10194018  0.09654105  0.08885164
   0.10336693  0.11065591  0.09689682  0.10539119]
 [ 0.09969486  0.10101629  0.09983859  0.09973694  0.10011305  0.10050438
   0.09950821  0.09971901  0.1003175   0.09955107]
 [ 0.10508666  0.08770984  0.11013029  0.10066471  0.09746905  0.08925749
   0.10433661  0.10111083  0.10190289  0.10233164]
 [ 0.1053774   0.07640396  0.10171271  0.11488824  0.109969    0.07305058
   0.12248608  0.10274819  0.08388286  0.109481  ]
 [ 0.09650233  0.08204421  0.10703861  0.10451381  0.10367602  0.08929945
   0.10522877  0.11235993  0.09552933  0.10380752]
 [ 0.09306367  0.05801263  0.10765588  0.11030831  0.10264575  0.0917316
   0.12237193  0.08927064  0.11435014  0.11058942]
 [ 0.08452509  0.02972044  0.09304042  0.21268865  0.

INFO:tensorflow:step = 101, loss = 2.29159 (18.512 sec)
INFO:tensorflow:probabilities = [[ 0.09987187  0.08838438  0.08975486  0.10517276  0.10359328  0.07775454
   0.11563658  0.10540441  0.10761844  0.10680882]
 [ 0.10710861  0.062641    0.11992186  0.11984371  0.09349209  0.05733605
   0.13090575  0.1029119   0.09259129  0.11324774]
 [ 0.10645904  0.06468724  0.10628371  0.1024859   0.10892671  0.05495496
   0.1145931   0.13289574  0.08724988  0.12146364]
 [ 0.09973882  0.07351809  0.10856744  0.10323674  0.10497875  0.08797063
   0.10832746  0.09635483  0.0971907   0.12011656]
 [ 0.09535932  0.05279597  0.10993297  0.14064844  0.0907146   0.02959797
   0.09150483  0.12323122  0.06289836  0.20331627]
 [ 0.09932057  0.10144053  0.09971256  0.09969687  0.10018722  0.10058113
   0.09933761  0.09976606  0.1004982   0.09945922]
 [ 0.11862524  0.0423611   0.09397662  0.12195152  0.0910749   0.06599832
   0.15905264  0.08875662  0.09724895  0.12095407]
 [ 0.1000734   0.05051512  0.09728427

INFO:tensorflow:global_step/sec: 5.29975
INFO:tensorflow:probabilities = [[ 0.13958569  0.03039466  0.09081697  0.14177658  0.08080605  0.03191095
   0.12615605  0.07723837  0.14724031  0.13407442]
 [ 0.1076185   0.03851756  0.12581408  0.12959453  0.11203316  0.03910413
   0.14364477  0.09210768  0.09543569  0.11612989]
 [ 0.09256199  0.06619822  0.11631458  0.09406514  0.1126541   0.07435577
   0.12802082  0.08654767  0.13297702  0.09630473]
 [ 0.11397097  0.04457086  0.13662264  0.13362898  0.08189796  0.04888522
   0.13913064  0.11363768  0.07402796  0.11362714]
 [ 0.05245747  0.01526257  0.17158085  0.08615812  0.08338675  0.03361238
   0.18770927  0.04753948  0.14899518  0.17329787]
 [ 0.08920068  0.03876906  0.13470119  0.14361081  0.07710902  0.05364924
   0.13666706  0.08363146  0.09478294  0.14787854]
 [ 0.09928329  0.10209663  0.09958796  0.09948664  0.10022476  0.10068643
   0.09921397  0.099693    0.10043445  0.09929292]
 [ 0.10913125  0.05729612  0.11764749  0.12235347  0

...

INFO:tensorflow:global_step/sec: 5.84748
INFO:tensorflow:probabilities = [[ 0.00000001  0.00116356  0.99658489  0.00031314  0.00000233  0.          0.
   0.00193385  0.00000052  0.00000167]
 [ 0.00000006  0.          0.          0.00000008  0.          0.99999774
   0.00000196  0.          0.00000001  0.00000012]
 [ 0.          0.00000083  0.00000273  0.99990118  0.00000003  0.00000329
   0.          0.00000015  0.0000595   0.00003227]
 [ 0.          0.          0.00028693  0.0002358   0.          0.
   0.00000009  0.          0.99947721  0.        ]
 [ 0.          0.00000013  0.00000001  0.00026857  0.0000006   0.          0.
   0.00001218  0.00000389  0.99971455]
 [ 0.          0.          0.99996257  0.00000007  0.          0.          0.
   0.0000374   0.          0.        ]
 [ 0.          0.00000178  0.          0.          0.9999882   0.00000005
   0.00000006  0.00000004  0.          0.00000983]
 [ 0.00000013  0.00000001  0.00000005  0.00000004  0.0000003   0.          0.
   0.9

INFO:tensorflow:step = 19901, loss = 0.0198982 (17.102 sec)
INFO:tensorflow:probabilities = [[ 0.00000003  0.00000011  0.00000002  0.00000763  0.          0.99994004
   0.00000008  0.00000091  0.0000414   0.00000973]
 [ 0.00000003  0.00001019  0.00010928  0.00000017  0.00000002  0.00000007
   0.00000002  0.00000003  0.99988019  0.00000001]
 [ 0.00000012  0.00000002  0.00000762  0.00002402  0.          0.          0.
   0.99996662  0.00000003  0.00000163]
 [ 0.          0.          0.          0.99999988  0.          0.00000008
   0.          0.          0.00000002  0.00000002]
 [ 0.00000007  0.99998569  0.00000178  0.00000014  0.0000004   0.00000002
   0.00000072  0.00000782  0.00000239  0.00000095]
 [ 0.          0.          0.          0.00000101  0.          0.99999905
   0.          0.          0.          0.        ]
 [ 0.          0.99999857  0.00000001  0.00000011  0.00000073  0.          0.
   0.00000048  0.          0.00000007]
 [ 0.00000002  0.99999309  0.0000002   0.00000062

INFO:tensorflow:Saving checkpoints for 20000 into tmp/lbp_cnn_mnist_2/model.ckpt.
INFO:tensorflow:Loss for final step: 0.0159689.
INFO:tensorflow:Starting evaluation at 2018-03-19-14:49:50
INFO:tensorflow:Restoring parameters from tmp/lbp_cnn_mnist_2/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-19-14:49:55
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9835, global_step = 20000, loss = 0.0546413
{'accuracy': 0.9835, 'loss': 0.054641303, 'global_step': 20000}


SystemExit: 

/Users/leosea/anaconda/envs/tensorflow/lib/python3.5/site-packages/IPython/core/interactiveshell.py:2870: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
